In [115]:
#Подключем необходимые для работы библиотеки
import pandas as pd
import geopandas as gpd
import folium
from shapely import geometry
from folium.plugins import MarkerCluster
from folium.plugins import MousePosition
from folium.plugins import Fullscreen
from folium.plugins import MiniMap

In [2]:
#Импортируем исходные данные: административная граница городского округа, пологины зданий и точечный слой с ОКН
adm_border = gpd.read_file('adm_border.geojson')
okn_points = gpd.read_file('OKN_points1.geojson')
buildings_polygons = gpd.read_file('buildings_polygons.geojson')


In [3]:
#Настраиваем проекцию в завивимости от зоны UTM города
adm_border = adm_border.to_crs("EPSG:32637")
okn_points = okn_points.to_crs("EPSG:32637")
buildings_polygons = buildings_polygons.to_crs("EPSG:32637")

In [8]:
#Удаляем лишние атрибуты в слое ОКН 
okn_points = okn_points[['field_1', 'Объект', 'Полный адрес', 'Категория историко-культурного значения', 'Вид объекта', 'Принадлежность к Юнеско', 'Особо ценный объект', 'дата создания', 'geometry']]



In [130]:
#Присоединяем информацию об ОКН к зданиям
buildings_polygons.crs = okn_points.crs
buildings_polygons = buildings_polygons.sjoin(okn_points)




In [105]:
#Создаем отдельный слой полигонов ОКН
buildings_polygons_okn = buildings_polygons[buildings_polygons['field_1'].notna()]
buildings_polygons_okn.head()

fid    osm_id  code    fclass                                        name  \
3     4  95936826  1500  building  Тульский коммунально-строительный техникум   
7     8  95936830  1500  building                                    Лицей №1   
10   11  95936833  1500  building                                         NaN   
14   15  95936839  1500  building                                         NaN   
14   15  95936839  1500  building                                         NaN   

          type                                           geometry  \
3          NaN  MULTIPOLYGON (((409439.394 6005324.392, 409455...   
7       school  MULTIPOLYGON (((409443.518 6005240.593, 409474...   
10         NaN  MULTIPOLYGON (((409528.497 6005340.271, 409543...   
14  apartments  MULTIPOLYGON (((409519.527 6005529.051, 409555...   
14  apartments  MULTIPOLYGON (((409519.527 6005529.051, 409555...   

    index_right  field_1                                             Объект  \
3            74       88  Здание Казенной палаты, где в 1866-1867 гг. сл...   
7           155      180                                   Духовное училище   
10           94      110                           Жилой дом В.П.Стрелковой   
14          220      255               Бывший жилой дом с торговлей Сисиных   
14          219      254                              Жилой дом Сальниковых   

                                         Полный адрес  \
3   Тульская область, г. Тула, проспект Ленина, д....   
7   Тульская область, г. Тула, улица Пушкинская, д...   
10  Тульская область, г. Тула, Центральный район, ...   
14  Тульская область, г. Тула, Центральный район, ...   
14  Тульская область, г. Тула, Центральный район, ...   

   Категория историко-культурного значения Вид объекта  \
3                    Федерального значения    Памятник   
7                   Регионального значения    Памятник   
10                  Регионального значения    Памятник   
14                  Регионального значения    Памятник   
14                  Регионального значения    Памятник   

   Принадлежность к Юнеско Особо ценный объект    дата создания  
3                      нет                 нет    1866-1867 гг.  
7                      нет                 нет    XVIII-XIX вв.  
10                     нет                 нет         XVIII в.  
14                     нет                 нет  XVIII - XIX вв.  
14                     нет                 нет         XVIII в.

In [129]:
#Создаем интерактивную карту
okn_points = okn_points.to_crs('EPSG:4326')
main_map = folium.Map(location=[okn_points.centroid.y.mean(), okn_points.centroid.x.mean()], zoom_start=12,  tiles="cartodb positron", control_scale=True)
main_map


In [107]:
#Настраиваем и добавляем слой с административной границей гороского округа Тула 
style1 = {'fillColor': 'grey', 'lineColor': 'red'}
folium.GeoJson(
    adm_border,
    name = "Граница городского округа Тула",
    style_function=lambda x:style1,
    highlight_function=lambda x: {"fillOpacity": 1},
    zoom_on_click=True,
    show=False,
).add_to(main_map)
main_map


In [108]:
#Настраиваем и добавляем слой с объектами культурного наследия
style2 = {'fillColor': 'red', 'lineColor': 'red'}
folium.GeoJson(
    buildings_polygons_okn,
    name = "Объекты культурного наследия",
    style_function=lambda x:style2,
    highlight_function=lambda x: {"fillOpacity": 0.05},
    zoom_on_click=True,
    show=False,
).add_to(main_map)
main_map

In [116]:
total_bounds = okn_points.total_bounds
minX, minY, maxX, maxY = total_bounds
square_size = 500
grid_sectror = []
x, y = (minX, minY)
geom_array = []

while y <= maxY:
        while x <= maxX:
            geom = geometry.Polygon([(x,y), (x, y+square_size), (x+square_size, y+square_size), (x+square_size, y), (x, y)])
            geom_array.append(geom)
            x += square_size
        x = minX
        y += square_size


grid = gpd.GeoDataFrame(geom_array, columns=['geometry']).set_crs('EPSG:32637')
grid['id'] = grid.index

In [123]:
okn_points=okn_points.to_crs("EPSG:32637")
merged = gpd.sjoin(okn_points, grid, how='left', predicate='within')
merged['n'] = 1
dissolve = merged.dissolve(by="index_right", aggfunc="count")
grid.loc[dissolve.index, 'n'] = dissolve.n.values

In [126]:
folium.Choropleth(
    geo_data=grid,
    data=grid,
    columns=['id', 'n'],
    fill_color='BuPu',
    fill_opacity = 0.7,
    key_on='id',
    nan_fill_opacity=0,
    line_color = "#0000",
    legend_name="Плотность ОКН",
    name='Плотность ОКН'
).add_to(main_map)
main_map

In [127]:
#Объединяем точки в кластеры на каждом мастабной уровне
marker_cluster = MarkerCluster(name='Кластеры ОКН')
c= folium.plugins.FeatureGroupSubGroup(marker_cluster, 'Кластеры ОКН')
main_map.add_child(marker_cluster)
main_map.add_child(mc1)
c.add_child(folium.GeoJson(okn_points.to_json(), embed=False, show=False))
main_map


In [128]:
#Подключем дополнительные опции и интерфейс
folium.LayerControl().add_to(v)
MousePosition().add_to(v)
Fullscreen(
    position="bottomright",
    title="Expand me",
    title_cancel="Exit me",
    force_separate_button=True,
).add_to(main_map)
MiniMap().add_to(main_map)
main_map

In [114]:
#Сохраняем финальную карту в файл
main_map.save("visualisation.html")